In [1]:
import glob
import os
import random
from typing import Union, List

import librosa
import numpy as np
import torch
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC, Wav2Vec2CTCTokenizer,  Wav2Vec2FeatureExtractor
import yaml
import json
from tqdm import tqdm
import pickle
import datasets

from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML

In [2]:
# Around 4000 data points
data_path = "asr_data.json"
with open(data_path, "r") as f:
    asr_data = json.load(f)

In [18]:
asr_data

[['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/1.wav', 'APPLE'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/10.wav',
  'THERE ARE TWO APPLES IN A WHITE BACKGROUND'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/100.wav',
  'THERE ARE THREE CUCUMBERS IN A BROWN BACKGROUND'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/101.wav', 'EGG'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/102.wav', 'EGGS'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/103.wav',
  'ONE EGG IN A WHITE BACKGROUND'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/104.wav',
  'THERE IS ONE EGG IN A WHITE BACKGROUND'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/105.wav',
  'ONE EGG IN A BLUE BACKGROUND'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/106.wav',
  'THERE IS ONE EGG IN A BLUE BACKGROUND'],
 ['/net/papilio/storage2/yhaoyuan/LAbyLM/audios_24k/11/107.wav',
  'ONE EGG IN A BROWN BACKGROUND'],
 ['/net/papilio/storage2/yh

In [2]:
import csv

In [3]:
LJSpeech_path = "/net/tateha/storage2/database/misc/LJSpeech"
wav_base_path = "/net/tateha/storage2/database/misc/LJSpeech/wavs/"
paired_data = LJSpeech_path + "/metadata.csv"

In [4]:
with open(paired_data, encoding="utf-8") as csv_file:
    csv_reader = csv.reader(csv_file, delimiter="|", quotechar=None, skipinitialspace=True)
    for row in csv_reader:
        uid, text, norm_text = row
        filename = f"{uid}.wav"
        example = {
            "id": uid,
            "file": os.path.join(wav_base_path, filename),
            "audio": os.path.join(wav_base_path, filename),
            "text": text,
            "normalized_text": norm_text,
        }
        # yield uid, example
        print(uid, example)

LJ001-0001 {'id': 'LJ001-0001', 'file': '/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0001.wav', 'audio': '/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0001.wav', 'text': 'Printing, in the only sense with which we are at present concerned, differs from most if not from all the arts and crafts represented in the Exhibition', 'normalized_text': 'Printing, in the only sense with which we are at present concerned, differs from most if not from all the arts and crafts represented in the Exhibition'}
LJ001-0002 {'id': 'LJ001-0002', 'file': '/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0002.wav', 'audio': '/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0002.wav', 'text': 'in being comparatively modern.', 'normalized_text': 'in being comparatively modern.'}
LJ001-0003 {'id': 'LJ001-0003', 'file': '/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0003.wav', 'audio': '/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0003.wav', 'text': 'For althou

In [15]:
with open(paired_data, "r") as f:
    paired_data = f.readlines()

In [30]:
LJSpeech_data = []
for data in paired_data:
    data = data.strip('\n')
    wav_path = wav_base_path + data.split("|")[0] + ".wav"
    trans = data.split("|")[1].upper()
    LJSpeech_data.append([wav_path, trans])

In [31]:
with open("asr_data_LJSpeech.json", "w") as f:
    json.dump(LJSpeech_data, f)

In [32]:
LJSpeech_data

[['/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0001.wav',
  'PRINTING, IN THE ONLY SENSE WITH WHICH WE ARE AT PRESENT CONCERNED, DIFFERS FROM MOST IF NOT FROM ALL THE ARTS AND CRAFTS REPRESENTED IN THE EXHIBITION'],
 ['/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0002.wav',
  'IN BEING COMPARATIVELY MODERN.'],
 ['/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0003.wav',
  'FOR ALTHOUGH THE CHINESE TOOK IMPRESSIONS FROM WOOD BLOCKS ENGRAVED IN RELIEF FOR CENTURIES BEFORE THE WOODCUTTERS OF THE NETHERLANDS, BY A SIMILAR PROCESS'],
 ['/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0004.wav',
  'PRODUCED THE BLOCK BOOKS, WHICH WERE THE IMMEDIATE PREDECESSORS OF THE TRUE PRINTED BOOK,'],
 ['/net/tateha/storage2/database/misc/LJSpeech/wavs/LJ001-0005.wav',
  'THE INVENTION OF MOVABLE METAL LETTERS IN THE MIDDLE OF THE FIFTEENTH CENTURY MAY JUSTLY BE CONSIDERED AS THE INVENTION OF THE ART OF PRINTING.'],
 ['/net/tateha/storage2/database/misc/LJSpeech/wavs/